# Libraries

In [1]:
# PATH to files of project
PATH = "../content/drive/MyDrive/Самообразование/GEO/"

In [2]:
pip install osmnx

In [3]:
!pip install pandas fiona shapely pyproj rtree

In [4]:
!pip install geopandas

In [5]:
import datetime

print("Последняя дата запуска:")
print(str(datetime.datetime.now()))

Последняя дата запуска:
2022-01-14 19:35:28.382185


In [6]:
import numpy as np
import pandas as pd
import math
from scipy import stats
import matplotlib.pyplot as plt
import seaborn as sns

In [7]:
from datetime import date
import calendar

In [8]:
import geopandas as gpd
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster 

In [9]:
from shapely.geometry import Polygon, shape, Point
from branca.element import Figure
import branca.colormap as cmp

In [10]:
pip install overpy

In [11]:
# Для геокодирования адресов
import geopy
from geopy.geocoders import Nominatim

In [12]:
import requests
import overpy

In [13]:
import osmnx as ox

In [14]:
from bs4 import BeautifulSoup

In [15]:
from math import cos, sin, asin, sqrt, radians

# User functions

In [16]:
def get_info(df):
    return pd.DataFrame({'Feature': df.columns.tolist(), 
                         'NaN_count': df.isna().sum().tolist(),
                         'Number_of_unique': pd.Series(df.columns.tolist()).apply(lambda row: df[row].nunique()),
                         'type': pd.Series(df.columns.tolist()).apply(lambda row: df[row].dtype)
    })

In [17]:
# For function "add_osm_features"
def calc_distance(lat1, lon1, lat2, lon2):
    """
    Calculate the great circle distance between two points
    on the earth (specified in decimal degrees)
    """
    # convert decimal degrees to radians
    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])
    # haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = sin(dlat / 2) ** 2 + cos(lat1) * cos(lat2) * sin(dlon / 2) ** 2
    c = 2 * asin(sqrt(a))
    km = 6371 * c
    return km

In [18]:
# For function add_osm_features
def agg_obj_around(gdf, dist, tags, osm_objs):
  '''
  Input: GeoDataFrame, Objects tag, Object dictionary 
  Result is a pivot table of OSM objects amount per address 
  '''

  # Group of objects 
  list_objects = [i for i in tags.keys()] 

  # Filter geodataframe with dist value
  gdf = gdf[gdf['dist_to_chosen_address_km'] <= dist]

  result_df = pd.DataFrame()
  
  for i in list_objects: 
    
    dic_obj = osm_objs[osm_objs['key'] == i]
    dic_obj.columns = ['obj', 'sub_obj']

    try: 
      sub_obj = pd.DataFrame(gdf[i].value_counts()).reset_index()
      sub_obj.columns = ['sub_obj', 'cnt']
    except: 
      sub_obj = pd.DataFrame(columns = ['sub_obj', 'cnt'])

    result = pd.merge(dic_obj, sub_obj, on='sub_obj', how='left').fillna(0) 
    result['full_feature_name'] = result['obj'] + "_" + result['sub_obj'] + "_" + str(dist) + "m"

    result_df = pd.concat([result_df, result])

  result_df = result_df[['full_feature_name', 'cnt']]

  return result_df  

# Data

### Offices

In [22]:
offices_msc = pd.read_csv(PATH+"data/"+"offices_msc.csv", index_col=[0])
offices_msc.head()

id    city        lat        lon   ntb
0   0  Moscow  55.685555  37.570230  1308
1   1  Moscow  55.737389  37.617949  2852
2   2  Moscow  55.723640  37.610586  1888
3   3  Moscow  55.788474  37.537555  1666
4   4  Moscow  55.893520  37.615400  1735

In [31]:
offices_msc.shape

(250, 5)

In [42]:
# Create the map
cluster_map = folium.Map(location=[55.76119684702124, 37.61683265249446], tiles='OpenStreetMap', zoom_start=12)

# Add points to the map
mc = MarkerCluster()

for idx, row in offices_msc.iterrows():
    if not math.isnan(row['lon']) and not math.isnan(row['lat']):
        mc.add_child(Marker([row['lat'], row['lon']]))

cluster_map.add_child(mc)

# Display the map
cluster_map

In [101]:
# Create a base map
m = folium.Map(location=[55.755884, 37.624386], tiles='OpenStreetMap', zoom_start=13)

for idx, row in offices_msc.iterrows(): 

    Marker([row['lat'], row['lon']], popup='office ' + str(row['id'])).add_to(m)

    Circle(
      location=[row['lat'], row['lon']],
      radius=row['ntb']/10, 
      color='blue').add_to(m)

# Display the map
m

The closer to the center, the greater the client flow. 

In [98]:
offices_msc.head()

id    city        lat        lon   ntb
0   0  Moscow  55.685555  37.570230  1308
1   1  Moscow  55.737389  37.617949  2852
2   2  Moscow  55.723640  37.610586  1888
3   3  Moscow  55.788474  37.537555  1666
4   4  Moscow  55.893520  37.615400  1735

### Vacancies

In [37]:
rent_places = pd.read_csv(PATH+'/data/'+'trade_points_cian_msc.csv', sep=';', index_col=[0])
rent_places.head()

address  ...                                             url
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
1  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
2  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
3  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
4  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/

[5 rows x 5 columns]

In [38]:
rent_places.shape

(4605, 5)

In [40]:
# Only address
addresses = rent_places['address'].drop_duplicates()
addresses

0      Москва, ЦАО, р-н Пресненский, наб. Пресненская...
9      Москва, ЦАО, р-н Пресненский, наб. Пресненская...
16     Москва, ЦАО, р-н Пресненский, наб. Пресненская...
21     Москва, СЗАО, р-н Хорошево-Мневники, Причальны...
28     Москва, ВАО, р-н Соколиная гора, Большая Семен...
                             ...                        
514    Москва, ВАО, р-н Соколиная гора, Малая Семенов...
518    Москва, ЦАО, р-н Басманный, Архангельский пер....
521    Москва, ЦАО, р-н Басманный, Старая Басманная у...
523    Москва, ЮЗАО, р-н Ломоносовский, Ленинский про...
526    Москва, САО, р-н Западное Дегунино, ул. Маршал...
Name: address, Length: 105, dtype: object

In [41]:
len(addresses)

105

### Addresses geocoding

#### Address parsing

In [ ]:
df_addresses = pd.DataFrame(addresses)
df_addresses['id_start_addr'] = df_addresses.index
df_addresses.head()

address  id_start_addr
0   Москва, ЦАО, р-н Пресненский, наб. Пресненская...              0
9   Москва, ЦАО, р-н Пресненский, наб. Пресненская...              9
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...             16
21  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...             21
28  Москва, ВАО, р-н Соколиная гора, Большая Семен...             28

In [ ]:
df_addresses['full_address'] = df_addresses['address']
df_addresses['city'] = df_addresses['address'].apply(lambda x: x.split(',')[0])
df_addresses['district'] = df_addresses['address'].apply(lambda x: x.split(',')[1])
df_addresses['area'] = df_addresses['address'].apply(lambda x: x.split(',')[2])
df_addresses['street'] = df_addresses['address'].apply(lambda x: x.split(',')[3])
df_addresses['number'] = df_addresses['address'].apply(lambda x: x.split(',')[4])

df_addresses['address_for_geocoding'] = df_addresses['city'] + ', ' + df_addresses['street'] + ', ' + df_addresses['number']

df_addresses.head()

address  ...                  address_for_geocoding
0   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         Москва,  наб. Пресненская,  12
9   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         Москва,  наб. Пресненская,  10
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...       Москва,  наб. Пресненская,  10с2
21  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...         Москва,  Причальный проезд,  2
28  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...  Москва,  Большая Семеновская ул.,  10

[5 rows x 9 columns]

In [ ]:
df_addresses['city'].value_counts()

Москва    105
Name: city, dtype: int64

In [ ]:
df_addresses['district'].value_counts()

 ЦАО                     31
 ВАО                     14
 САО                     11
 ЮАО                     10
 СВАО                    10
 ЮЗАО                     7
 СЗАО                     6
 ЮВАО                     6
 ЗАО                      5
 НАО (Новомосковский)     4
 ТАО (Троицкий)           1
Name: district, dtype: int64

In [ ]:
df_addresses['street'].value_counts()

 Ленинский просп.           3
 просп. Мира                3
 наб. Пресненская           3
 Бауманская ул.             2
 Большая Семеновская ул.    2
                           ..
 Тагильская ул.             1
 Первомайская ул.           1
 ул. Академика Янгеля       1
 ул. Коминтерна             1
 Ташкентская ул.            1
Name: street, Length: 91, dtype: int64

#### Geocoding with Nominatim

In [ ]:
#making an instance of Nominatim class
geolocator = Nominatim(user_agent="my_request")

#applying geocode method to get the location
location = geolocator.geocode(loc)

In [ ]:
loc = rent_places.iloc[0, 0]
loc

'Москва, ЦАО, р-н Пресненский, наб. Пресненская, 12'

In [ ]:
location = geolocator.geocode('Moscow, Presnenskaya 12')

In [ ]:
location = geolocator.geocode('Москва, наб. Пресненская 12')
location

Location(Комплекс «Федерация» - Европа, 12, Пресненская набережная, Шелепиха, Пресненский район, Москва, Центральный федеральный округ, 123112, Россия, (55.74945185, 37.53701338298765, 0.0))

In [ ]:
print((location.latitude, location.longitude))

(55.74945185, 37.53701338298765)


In [ ]:
df_addresses['coord'] = df_addresses['address_for_geocoding'].apply(lambda x: geolocator.geocode(x)) 

df_addresses.head()

address  ...                                              coord
0   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  (Комплекс «Федерация» - Европа, 12, Пресненска...
9   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  (Башня «Евразия», 10 с1, Пресненская набережна...
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...                                               None
21  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...  (Причальный проезд, Шелепиха, Пресненский райо...
28  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...  (10, Большая Семёновская улица, район Соколина...

[5 rows x 10 columns]

In [ ]:
df_addresses['latitude'] = df_addresses['coord'].apply(lambda x: x.latitude if x is not None else np.nan) 
df_addresses['longtitude'] = df_addresses['coord'].apply(lambda x: x.longitude if x is not None else np.nan) 

df_addresses.head()

address  ...  longtitude
0   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...   37.537013
9   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...   37.535369
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
21  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...   37.519274
28  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...   37.702644

[5 rows x 12 columns]

Number of not geocoded items:

In [ ]:
df_addresses[df_addresses['coord'].isna()].shape

(28, 12)

28 addresses were not geocoded

In [ ]:
df_addresses[df_addresses['coord'].isna()]

address  ...  longtitude
16   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
37   Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...         NaN
45   Москва, ЦАО, р-н Замоскворечье, Большая Татарс...  ...         NaN
59   Москва, ЦАО, р-н Тверской, ул. Каретный Ряд, 5...  ...         NaN
88   Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN
91    Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...         NaN
110  Москва, САО, р-н Западное Дегунино, Дмитровско...  ...         NaN
112  Москва, ЦАО, р-н Мещанский, Олимпийский просп....  ...         NaN
119  Москва, ЦАО, р-н Тверской, Старопименовский пе...  ...         NaN
229  Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...         NaN
235      Москва, ЦАО, р-н Мещанский, просп. Мира, 92С1  ...         NaN
241  Москва, ЦАО, р-н Басманный, Бакунинская ул., 72С2  ...         NaN
248  Москва, ТАО (Троицкий), Первомайское поселение...  ...         NaN
280  Москва, ЮАО, р-н Орехово-Борисово Южное, ул. Г...  ...         NaN
300  Москва, ЦАО, р-н Басманный, ул. Госпитальный В...  ...         NaN
316     Москва, ВАО, р-н Перово, Электродная ул., 2С32  ...         NaN
321  Москва, ВАО, р-н Соколиная гора, Ткацкая ул., 5С4  ...         NaN
334       Москва, САО, р-н Аэропорт, Часовая ул., 16С1  ...         NaN
344  Москва, НАО (Новомосковский), Сосенское поселе...  ...         NaN
350  Москва, ЦАО, р-н Пресненский, ул. Грузинский В...  ...         NaN
357  Москва, ЮВАО, р-н Выхино-Жулебино, Ташкентская...  ...         NaN
375     Москва, САО, р-н Сокол, Новопесчаная ул., 23К7  ...         NaN
379       Москва, СЗАО, р-н Митино, Пятницкое ш., 15к4  ...         NaN
384    Москва, ЮВАО, р-н Люблино, Люблинская ул., 76к5  ...         NaN
439  Москва, ЮВАО, р-н Печатники, Волгоградский про...  ...         NaN
510  Москва, ЮВАО, р-н Южнопортовый, Волгоградский ...  ...         NaN
514  Москва, ВАО, р-н Соколиная гора, Малая Семенов...  ...         NaN
518  Москва, ЦАО, р-н Басманный, Архангельский пер....  ...         NaN

[28 rows x 12 columns]

In [ ]:
location = geolocator.geocode('Москва, Дмитровское ш., 73 с1')
location

Location(73 с1, Дмитровское шоссе, район Западное Дегунино, Москва, Центральный федеральный округ, 125635, Россия, (55.85708425, 37.558889039749076, 0.0))

In [ ]:
df_not_geocoded = df_addresses[df_addresses['coord'].isna()]
df_not_geocoded.head()

address  ...  longtitude
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
37  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...         NaN
45  Москва, ЦАО, р-н Замоскворечье, Большая Татарс...  ...         NaN
59  Москва, ЦАО, р-н Тверской, ул. Каретный Ряд, 5...  ...         NaN
88  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN

[5 rows x 12 columns]

In [ ]:
df_not_geocoded['number'] = df_not_geocoded['number'].apply(lambda x: x.replace("С", "с") if 'С' in x else x)
df_not_geocoded['number'] = df_not_geocoded['number'].apply(lambda x: x.replace("с", " с") if 'с' in x else x)

df_not_geocoded['number'] = df_not_geocoded['number'].apply(lambda x: x.replace("К", "к") if 'К' in x else x)
df_not_geocoded['number'] = df_not_geocoded['number'].apply(lambda x: x.replace("к", " к") if 'к' in x else x)


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documen

In [ ]:
df_not_geocoded.head()

address  ...  longtitude
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
37  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...         NaN
45  Москва, ЦАО, р-н Замоскворечье, Большая Татарс...  ...         NaN
59  Москва, ЦАО, р-н Тверской, ул. Каретный Ряд, 5...  ...         NaN
88  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN

[5 rows x 12 columns]

In [ ]:
df_not_geocoded['address_for_geocoding'] = df_not_geocoded['city'] + ', ' + df_not_geocoded['street'] + ', ' + df_not_geocoded['number']

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [ ]:
df_not_geocoded.head()

address  ...  longtitude
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
37  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...         NaN
45  Москва, ЦАО, р-н Замоскворечье, Большая Татарс...  ...         NaN
59  Москва, ЦАО, р-н Тверской, ул. Каретный Ряд, 5...  ...         NaN
88  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN

[5 rows x 12 columns]

In [ ]:
df_not_geocoded['coord'] = df_not_geocoded['address_for_geocoding'].apply(lambda x: geolocator.geocode(x)) 
df_not_geocoded.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


address  ...  longtitude
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
37  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...         NaN
45  Москва, ЦАО, р-н Замоскворечье, Большая Татарс...  ...         NaN
59  Москва, ЦАО, р-н Тверской, ул. Каретный Ряд, 5...  ...         NaN
88  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN

[5 rows x 12 columns]

In [ ]:
df_not_geocoded['latitude'] = df_not_geocoded['coord'].apply(lambda x: x.latitude if x is not None else np.nan) 
df_not_geocoded['longtitude'] = df_not_geocoded['coord'].apply(lambda x: x.longitude if x is not None else np.nan) 

df_not_geocoded.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


address  ...  longtitude
16  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
37  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...   37.702108
45  Москва, ЦАО, р-н Замоскворечье, Большая Татарс...  ...   37.632637
59  Москва, ЦАО, р-н Тверской, ул. Каретный Ряд, 5...  ...   37.609079
88  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN

[5 rows x 12 columns]

not geocoded:

In [ ]:
df_not_geocoded[df_not_geocoded['coord'].isna()]

address  ...  longtitude
16   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
88   Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN
91    Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...         NaN
229  Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...         NaN
248  Москва, ТАО (Троицкий), Первомайское поселение...  ...         NaN
344  Москва, НАО (Новомосковский), Сосенское поселе...  ...         NaN

[6 rows x 12 columns]

In [ ]:
df_not_geocoded[df_not_geocoded['coord'].isna()].shape

(6, 12)

Manually corrected addresses

In [ ]:
list_not_geocoded = df_not_geocoded[df_not_geocoded['coord'].isna()]['address'].tolist()

list_not_geocoded_coord = [
 (55.7475355, 37.5348988686347),
 (55.6389274, 37.641323),
 (55.8428476, 37.6463735), 
 (55.770588, 37.604897),
 (55.544311, 37.154464),
 (55.601305, 37.411346)  
]



In [ ]:
df_not_geocoded2 = pd.DataFrame({'address': list_not_geocoded,
                                 'coord': list_not_geocoded_coord})


df_not_geocoded2['latitude'] = df_not_geocoded2['coord'].apply(lambda x: x[0] if x is not None else np.nan) 
df_not_geocoded2['longtitude'] = df_not_geocoded2['coord'].apply(lambda x: x[1] if x is not None else np.nan) 

In [ ]:
df_not_geocoded2

address  ... longtitude
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.534899
1  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...  37.641323
2   Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...  37.646374
3  Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...  37.604897
4  Москва, ТАО (Троицкий), Первомайское поселение...  ...  37.154464
5  Москва, НАО (Новомосковский), Сосенское поселе...  ...  37.411346

[6 rows x 4 columns]

Gather data

In [ ]:
df_not_geocoded[df_not_geocoded['coord'].isna()]

address  ...  longtitude
16   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...         NaN
88   Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...         NaN
91    Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...         NaN
229  Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...         NaN
248  Москва, ТАО (Троицкий), Первомайское поселение...  ...         NaN
344  Москва, НАО (Новомосковский), Сосенское поселе...  ...         NaN

[6 rows x 12 columns]

In [ ]:
df_not_geocoded2.head()

address  ... longtitude
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.534899
1  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...  37.641323
2   Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...  37.646374
3  Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...  37.604897
4  Москва, ТАО (Троицкий), Первомайское поселение...  ...  37.154464

[5 rows x 4 columns]

In [ ]:
df_not_geocoded2 = df_not_geocoded[df_not_geocoded['coord'].isna()].drop(columns=['coord', 'latitude', 'longtitude']).merge(df_not_geocoded2, left_on='address', right_on='address')
df_not_geocoded2.head()

address  ...  longtitude
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...   37.534899
1  Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...   37.641323
2   Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...   37.646374
3  Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...   37.604897
4  Москва, ТАО (Троицкий), Первомайское поселение...  ...   37.154464

[5 rows x 12 columns]

In [ ]:
df_manually_geocoded = pd.concat([df_not_geocoded[~df_not_geocoded['coord'].isna()], df_not_geocoded2], axis=0)
df_manually_geocoded

address  ...  longtitude
37   Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...   37.702108
45   Москва, ЦАО, р-н Замоскворечье, Большая Татарс...  ...   37.632637
59   Москва, ЦАО, р-н Тверской, ул. Каретный Ряд, 5...  ...   37.609079
110  Москва, САО, р-н Западное Дегунино, Дмитровско...  ...   37.558889
112  Москва, ЦАО, р-н Мещанский, Олимпийский просп....  ...   37.624472
119  Москва, ЦАО, р-н Тверской, Старопименовский пе...  ...   37.604731
235      Москва, ЦАО, р-н Мещанский, просп. Мира, 92С1  ...   37.635759
241  Москва, ЦАО, р-н Басманный, Бакунинская ул., 72С2  ...   37.696806
280  Москва, ЮАО, р-н Орехово-Борисово Южное, ул. Г...  ...   37.726133
300  Москва, ЦАО, р-н Басманный, ул. Госпитальный В...  ...   37.704501
316     Москва, ВАО, р-н Перово, Электродная ул., 2С32  ...   37.752430
321  Москва, ВАО, р-н Соколиная гора, Ткацкая ул., 5С4  ...   37.722508
334       Москва, САО, р-н Аэропорт, Часовая ул., 16С1  ...   37.535607
350  Москва, ЦАО, р-н Пресненский, ул. Грузинский В...  ...   37.581258
357  Москва, ЮВАО, р-н Выхино-Жулебино, Ташкентская...  ...   37.806062
375     Москва, САО, р-н Сокол, Новопесчаная ул., 23К7  ...   37.512956
379       Москва, СЗАО, р-н Митино, Пятницкое ш., 15к4  ...   37.378911
384    Москва, ЮВАО, р-н Люблино, Люблинская ул., 76к5  ...   37.729354
439  Москва, ЮВАО, р-н Печатники, Волгоградский про...  ...   37.668967
510  Москва, ЮВАО, р-н Южнопортовый, Волгоградский ...  ...   37.690109
514  Москва, ВАО, р-н Соколиная гора, Малая Семенов...  ...   37.717449
518  Москва, ЦАО, р-н Басманный, Архангельский пер....  ...   37.637409
0    Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...   37.534899
1    Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...   37.641323
2     Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...   37.646374
3    Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...   37.604897
4    Москва, ТАО (Троицкий), Первомайское поселение...  ...   37.154464
5    Москва, НАО (Новомосковский), Сосенское поселе...  ...   37.411346

[28 rows x 12 columns]

In [ ]:
df_manually_geocoded.shape

(28, 12)

Prepared data: 

In [ ]:
df_addresses_prepared = pd.concat([df_addresses[~df_addresses['coord'].isna()], df_manually_geocoded], axis=0)
df_addresses_prepared

address  ...  longtitude
0   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...   37.537013
9   Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...   37.535369
21  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...   37.519274
28  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...   37.702644
42       Москва, ЦАО, р-н Тверской, Тверская ул., 8к1  ...   37.612124
..                                                ...  ...         ...
1   Москва, ЮАО, р-н Москворечье-Сабурово, пер. 1-...  ...   37.641323
2    Москва, СВАО, р-н Ростокино, ул. 1-я Леонова, 18  ...   37.646374
3   Москва, ЦАО, р-н Тверской, ул. Малая Дмитровка...  ...   37.604897
4   Москва, ТАО (Троицкий), Первомайское поселение...  ...   37.154464
5   Москва, НАО (Новомосковский), Сосенское поселе...  ...   37.411346

[105 rows x 12 columns]

In [ ]:
# save addresses 
# df_addresses_prepared.to_csv(PATH+'rent_addresses_prepared.csv')

#### Load result with geocoded addresses

In [43]:
df_addresses_prepared = pd.read_csv(PATH+'rent_addresses_prepared.csv', index_col=[0])
df_addresses_prepared = df_addresses_prepared.drop(columns=['full_address','id_start_addr'])
df_addresses_prepared = df_addresses_prepared.reset_index(drop=True)
df_addresses_prepared.head()

address  ... longtitude
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.537013
1  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.535369
2  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...  37.519274
3  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...  37.702644
4       Москва, ЦАО, р-н Тверской, Тверская ул., 8к1  ...  37.612124

[5 rows x 10 columns]

In [45]:
# Create a map
m = folium.Map(location=[55.75380277393858, 37.62337139487209], tiles='OpenStreetMap', zoom_start=13)

# Add points to the map
for idx, row in df_addresses_prepared.iterrows():
    Marker([row['latitude'], row['longtitude']], popup=row['address'], icon=folium.Icon(color='red')).add_to(m)

# Display the map
m

Соединим координаты с объектами аренды

In [ ]:
rent_places.head()

address  ...                                             url
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
1  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
2  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
3  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/
4  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  https://www.cian.ru/rent/commercial/263310459/

[5 rows x 5 columns]

In [ ]:
df_rent_places = rent_places.merge(df_addresses_prepared[['address', 'latitude', 'longtitude']], on='address', how='left')
df_rent_places.head()

address  ... longtitude
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.537013
1  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.537013
2  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.537013
3  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.537013
4  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.537013

[5 rows x 7 columns]

In [ ]:
get_info(df_rent_places)

Feature  NaN_count  Number_of_unique     type
0     address          0               105   object
1        area          0               301   object
2  metr_price          0               243   object
3       price          0               348   object
4         url          0               118   object
5    latitude          0               103  float64
6  longtitude          0               103  float64

### OSM objects

#### OSM objects dictionary https://wiki.openstreetmap.org/wiki/RU:Объекты_карты

In [ ]:
PATH

'../content/drive/MyDrive/Самообразование/GEO/'

In [ ]:
# Parsing of saved web-page html
with open(PATH+"osm_objects.html", "r", encoding='utf-8') as f:
    html_string = f.read()

In [ ]:
html_string

'\n<!DOCTYPE html>\n<html class="client-nojs" lang="ru" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>RU:Объекты карты — OpenStreetMap Wiki</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"64a011235f4a3d74993d38d2","wgCSPNonce":!1,"wgCanonicalNamespace":"RU","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":210,"wgPageName":"RU:Объекты_карты","wgTitle":"Объекты карты","wgCurRevisionId":2067788,"wgRevisionId":2067788,"wgArticleId":11931,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Pages where template include size is exceeded","Pages with too many expensive parser function calls","Pages with script errors","RU:Proposals admin","RU:Referen

In [ ]:
soup = BeautifulSoup(html_string, 'lxml') # Parse the HTML as a string

list_of_tables = soup.find_all(class_='wikitable') # soup.find_all('table')

In [ ]:
len(list_of_tables)

23

In [ ]:
list_of_tables[0]

<table border="1" cellpadding="2" cellspacing="0" class="wikitable">
<tbody><tr style="background-color:#F8F4C2">
<th style="width:70px">Ключ
</th>
<th style="width:100px">Значение
</th>
<th style="width:70px">Элементы
</th>
<th>Описание
</th>
<th style="width:100px">Обозначение (Osmarender)
</th>
<th style="width:100px">Фото
</th></tr>
<tr>
<th colspan="7" style="border-bottom: 3px double;">
<h4><span id="Дороги"></span><span class="mw-headline" id=".D0.94.D0.BE.D1.80.D0.BE.D0.B3.D0.B8">Дороги</span></h4>
</th></tr>
<tr>
<th colspan="7">
<p>Основные теги для дорожной сети, от наиболее значимых к наименее значимым
</p>
</th></tr>
<tr>
<td><a href="/wiki/RU:Key:highway" title="RU:Key:highway"> highway</a>
</td>
<td><a href="/wiki/RU:Tag:highway%3Dmotorway" title="RU:Tag:highway=motorway"> motorway</a>
</td>
<td><a href="/wiki/RU:%D0%9B%D0%B8%D0%BD%D0%B8%D1%8F" title="линия"><img alt="линия" decoding="async" height="20" src="/w/images/thumb/e/ee/Osm_element_way.svg/20px-Osm_element_way.s

In [ ]:
def get_table_from_html(table_html):
  '''
  На входе - HTML страницы с таблицей в формате str
  Ф-ция выводит датафрейм спрасенных данных по объектам OSM 
  '''
 
  output_rows = []

  for table_row in table_html.find_all('tr'):
      columns = table_row.find_all('td')
      output_row = []
      for column in columns:
          output_row.append(column.text)
      output_rows.append(output_row)

  return pd.DataFrame(output_rows)[[0,1]] # берем первые два столбца - key и value 


In [ ]:
# all finded tables

df_osm_obj = pd.DataFrame(columns=[0,1])

for i in list_of_tables: 
  df_osm_obj = pd.concat([df_osm_obj, get_table_from_html(i)])

df_osm_obj.columns = ['key', 'value'] 

In [ ]:
# Cleaning 

df_osm_obj = df_osm_obj.dropna().drop_duplicates().reset_index(drop=True)

df_osm_obj['key'] = df_osm_obj['key'].str.strip()
df_osm_obj['value'] = df_osm_obj['value'].str.strip()

df_osm_obj

key                   value
0         highway                motorway
1         highway                   trunk
2         highway                 primary
3         highway               secondary
4         highway                tertiary
...           ...                     ...
1060     boundary   special_economic_zone
1061     boundary  Задаётся пользователем
1062  admin_level                 (число)
1063  border_type                       *
1064   start_date                  (дата)

[1065 rows x 2 columns]

In [ ]:
# Delete some values: 
df_osm_obj = df_osm_obj[(df_osm_obj['key'] != 'start_date') & (df_osm_obj['key'] != 'admin_level') & (df_osm_obj['key'] != 'border_type')] # keys 

In [ ]:
# Replace value
df_osm_obj['value'] = df_osm_obj['value'].replace(['Задаётся пользователем', 'user defined', 'Определяется пользователем', 'Своё значение', 'По выбору пользователя', 'User Defined', 'User defined', 'user_defined'],'user_defined')
df_osm_obj

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


key                  value
0      highway               motorway
1      highway                  trunk
2      highway                primary
3      highway              secondary
4      highway               tertiary
...        ...                    ...
1057  boundary              political
1058  boundary            postal_code
1059  boundary         protected_area
1060  boundary  special_economic_zone
1061  boundary           user_defined

[1061 rows x 2 columns]

In [ ]:
df_osm_obj['key'].value_counts()

shop               169
amenity            120
building            80
man_made            62
craft               58
                  ... 
traffic_calming      1
tactile_paving       1
smoothness           1
sac_scale            1
height               1
Name: key, Length: 88, dtype: int64

In [ ]:
# save result
# df_osm_obj.to_csv(PATH+'dic_osm_object.csv')

#### Load prepared OSM objects dictionary

In [56]:
df_osm_obj = pd.read_csv(PATH+'dic_osm_object.csv', index_col=[0])
df_osm_obj.head()

key      value
0  highway   motorway
1  highway      trunk
2  highway    primary
3  highway  secondary
4  highway   tertiary

In [57]:
df_osm_obj['key'].value_counts()

shop               169
amenity            120
building            80
man_made            62
craft               58
                  ... 
traffic_calming      1
tactile_paving       1
smoothness           1
sac_scale            1
height               1
Name: key, Length: 88, dtype: int64

In [58]:
df_osm_obj[df_osm_obj['key'] == 'shop']

key             value
680  shop           alcohol
681  shop            bakery
682  shop         beverages
683  shop  brewing_supplies
684  shop           butcher
..    ...               ...
844  shop     travel_agency
845  shop            vacant
846  shop           weapons
847  shop           outpost
848  shop      user_defined

[169 rows x 2 columns]

In [59]:
# Clean tags list
list_of_tags = [i for i in df_osm_obj['key'].unique().tolist() if ":" not in i]
list_of_tags

['highway',
 'footway',
 'sidewalk',
 'cycleway',
 'busway',
 'abutters',
 'bicycle_road',
 'bus_bay',
 'destination',
 'embankment',
 'embedded_rails',
 'ford',
 'ice_road',
 'incline',
 'junction',
 'lanes',
 'lit',
 'maxspeed',
 'motorroad',
 'mountain_pass',
 'oneway',
 'overtaking',
 'passing_places',
 'priority_road',
 'sac_scale',
 'service',
 'smoothness',
 'surface',
 'tactile_paving',
 'tracktype',
 'traffic_calming',
 'trail_visibility',
 'trailblazed',
 'turn',
 'width',
 'winter_road',
 'emergency',
 'barrier',
 'building',
 'entrance',
 'height',
 'non_existent_levels',
 'soft_storey',
 'waterway',
 'intermittent',
 'seasonal',
 'lock',
 'mooring',
 'usage',
 'tunnel',
 'bridge',
 'railway',
 'cutting',
 'electrified',
 'frequency',
 'tracks',
 'voltage',
 'public_transport',
 'landuse',
 'aeroway',
 'airmark',
 'aerialway',
 'power',
 'line',
 'man_made',
 'leisure',
 'amenity',
 'shop',
 'craft',
 'tourism',
 'military',
 'natural',
 'route',
 'boundary']

In [60]:
# Make dictionary
tags = dict.fromkeys(list_of_tags, True)
tags

{'abutters': True,
 'aerialway': True,
 'aeroway': True,
 'airmark': True,
 'amenity': True,
 'barrier': True,
 'bicycle_road': True,
 'boundary': True,
 'bridge': True,
 'building': True,
 'bus_bay': True,
 'busway': True,
 'craft': True,
 'cutting': True,
 'cycleway': True,
 'destination': True,
 'electrified': True,
 'embankment': True,
 'embedded_rails': True,
 'emergency': True,
 'entrance': True,
 'footway': True,
 'ford': True,
 'frequency': True,
 'height': True,
 'highway': True,
 'ice_road': True,
 'incline': True,
 'intermittent': True,
 'junction': True,
 'landuse': True,
 'lanes': True,
 'leisure': True,
 'line': True,
 'lit': True,
 'lock': True,
 'man_made': True,
 'maxspeed': True,
 'military': True,
 'mooring': True,
 'motorroad': True,
 'mountain_pass': True,
 'natural': True,
 'non_existent_levels': True,
 'oneway': True,
 'overtaking': True,
 'passing_places': True,
 'power': True,
 'priority_road': True,
 'public_transport': True,
 'railway': True,
 'route': True,


#### Find OSM objects for one address

In [92]:
# one office: 
df_addresses_prepared.loc[df_addresses_prepared.index == 4]

address    city  ...   latitude longtitude
4  Москва, ЦАО, р-н Тверской, Тверская ул., 8к1  Москва  ...  55.758778  37.612124

[1 rows x 10 columns]

In [93]:
one_office_address = 'Москва, Тверская ул., 8к1'
one_office_latitude = 55.758778
one_office_longtitude = 37.612124

In [78]:
tags_for_one_office = {'shop': True, 'amenity': True}

In [79]:
gdf_obj_around = ox.geometries.geometries_from_point((one_office_latitude, one_office_longtitude), tags_for_one_office, dist=500).reset_index()
gdf_obj_around.head()

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):


element_type      osmid  ... education_profile:general ref:temples.ru
0         node  447645709  ...                       NaN            NaN
1         node  447645714  ...                       NaN            NaN
2         node  529550637  ...                       NaN            NaN
3         node  529550639  ...                       NaN            NaN
4         node  529550640  ...                       NaN            NaN

[5 rows x 274 columns]

In [90]:
# Cafes around
cafes = gdf_obj_around[(gdf_obj_around["amenity"] == "cafe") & (gdf_obj_around["element_type"] == 'node')].dropna(axis=1, how="any").drop(columns=['osmid'])
cafes['longtitude'] = cafes['geometry'].x
cafes['latitude'] = cafes['geometry'].y
cafes.head()

element_type                   geometry  ... longtitude   latitude
0          node  POINT (37.61452 55.76043)  ...  37.614516  55.760427
10         node  POINT (37.61734 55.75898)  ...  37.617342  55.758984
14         node  POINT (37.60888 55.75942)  ...  37.608880  55.759420
21         node  POINT (37.60582 55.75663)  ...  37.605815  55.756631
26         node  POINT (37.60692 55.76299)  ...  37.606922  55.762990

[5 rows x 6 columns]

In [91]:
# markets around
markets = gdf_obj_around[(gdf_obj_around["shop"].isna() == False) & (gdf_obj_around["element_type"] == 'node')].dropna(axis=1, how="any").drop(columns=['osmid'])
markets['longtitude'] = markets['geometry'].x
markets['latitude'] = markets['geometry'].y
markets.head()

element_type                   geometry         shop  longtitude   latitude
1          node  POINT (37.60891 55.76254)        books   37.608913  55.762539
10         node  POINT (37.61734 55.75898)          tea   37.617342  55.758984
22         node  POINT (37.61369 55.75989)  convenience   37.613688  55.759893
24         node  POINT (37.61244 55.75919)       beauty   37.612440  55.759186
25         node  POINT (37.61427 55.75775)      clothes   37.614271  55.757746

In [97]:
# Create a map
m = folium.Map(location=[one_office_latitude, one_office_longtitude], tiles='OpenStreetMap', zoom_start=13)

cafes_group = folium.FeatureGroup(name='Cafe')
markets_group = folium.FeatureGroup(name='Market')


# add one office 
Marker([one_office_latitude, one_office_longtitude], popup=one_office_address, icon=folium.Icon(color='red')).add_to(m)

# Add cafes to the map
for idx, row in cafes.iterrows():
    Marker([row['latitude'], row['longtitude']], popup='Cafe '+row['name'], icon=folium.Icon(color='blue')).add_to(cafes_group) #.add_to(m)

# Add cafes to the map
for idx, row in markets.iterrows():
    Marker([row['latitude'], row['longtitude']], popup='Market '+row['shop'], icon=folium.Icon(color='orange')).add_to(markets_group) #.add_to(m)

m.add_child(cafes_group)
m.add_child(markets_group)

# turn on layer control
m.add_child(folium.map.LayerControl())

# Display the map
m

#### Downloading OSM objects for vacancies addresses

In [ ]:
df_addresses_prepared.head()

address  ... longtitude
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.537013
1  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...  37.535369
2  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...  37.519274
3  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...  37.702644
4       Москва, ЦАО, р-н Тверской, Тверская ул., 8к1  ...  37.612124

[5 rows x 10 columns]

In [ ]:
# создаем столбец id_address_rent
df_addresses_prepared['id_address_rent'] = df_addresses_prepared.index
df_addresses_prepared.head()

address  ... id_address_rent
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...               0
1  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...               1
2  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...               2
3  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...               3
4       Москва, ЦАО, р-н Тверской, Тверская ул., 8к1  ...               4

[5 rows x 11 columns]

In [ ]:
df_addr_rent = df_addresses_prepared[['id_address_rent', 'address_for_geocoding', 'latitude', 'longtitude']]
df_addr_rent.head()

id_address_rent  ... longtitude
0                0  ...  37.537013
1                1  ...  37.535369
2                2  ...  37.519274
3                3  ...  37.702644
4                4  ...  37.612124

[5 rows x 4 columns]

In [ ]:
# For function add_osm_features

def calc_distance(lat1, lon1, lat2, lon2):
    """
    Calculate the great circle distance between two points
    on the earth (specified in decimal degrees)
    """
    # convert decimal degrees to radians
    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])
    # haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = sin(dlat / 2) ** 2 + cos(lat1) * cos(lat2) * sin(dlon / 2) ** 2
    c = 2 * asin(sqrt(a))
    km = 6371 * c
    return km

In [ ]:
# For function add_osm_features

def agg_obj_around(gdf, dist, tags, osm_objs):
  '''
  На входе: геодатафрэйм, тэги объектов, таблица-словарь 
  Функция подсчитывает, сколько объектов каждого тэга есть в геодатасэте в разрезе расстояния. 
  Выводит сводную таблицу по кол-ву объектов
  '''

  # Group of objects 
  list_objects = [i for i in tags.keys()] 

  # Filter data
  gdf = gdf[gdf['dist_to_chosen_address_km'] <= dist]

  result_df = pd.DataFrame()
  
  for i in list_objects: 
    
    # Objects and subobjects table
    dic_obj = osm_objs[osm_objs['key'] == i]
    dic_obj.columns = ['obj', 'sub_obj']

    # subobjects in dataframe 
    try: 
      sub_obj = pd.DataFrame(gdf[i].value_counts()).reset_index()
      sub_obj.columns = ['sub_obj', 'cnt']
    except: 
      sub_obj = pd.DataFrame(columns = ['sub_obj', 'cnt'])

    # number of subobjects 
    result = pd.merge(dic_obj, sub_obj, on='sub_obj', how='left').fillna(0) 
    result['full_feature_name'] = result['obj'] + "_" + result['sub_obj'] + "_" + str(dist) + "m"

    result_df = pd.concat([result_df, result])

  result_df = result_df[['full_feature_name', 'cnt']]

  return result_df  

In [ ]:
def add_osm_features(df, dist, tags, df_dic_osm_obj): 

  gdf_result = gpd.GeoDataFrame()

  for idx, row in df.iterrows(): 

    try: 
    
      gdf = ox.geometries.geometries_from_point((row['latitude'], row['longtitude']), tags, dist=dist).reset_index() 

      gdf["centroid"] = gdf.geometry.centroid

      # Centr
      gdf['lat_centre_of_object'] = gdf['centroid'].y
      gdf['lon_centre_of_object'] = gdf['centroid'].x
  
      gdf['lat_chosen_address'] = row['latitude']
      gdf['lon_chosen_address'] = row['longtitude']

      gdf['dist_to_chosen_address_km'] = gdf.apply(lambda row: calc_distance(row['lat_centre_of_object'], row['lon_centre_of_object'], row['lat_chosen_address'], row['lon_chosen_address']), axis=1)  

      objs_around = agg_obj_around(gdf, dist, tags, df_dic_osm_obj)
    
      objs_around = objs_around.T.reset_index(drop=True)
      new_header = objs_around.iloc[0] #grab the first row for the header
      objs_around = objs_around[1:]    #take the data less the header row
      objs_around.columns = new_header #set the header row as the df header

      objs_around['id_address'] = idx 
      objs_around['address'] = row['address_for_geocoding'] 
      objs_around['latitude'] = row['latitude'] 
      objs_around['longtitude'] = row['longtitude']

      gdf_result = pd.concat([gdf_result, objs_around], axis=0)
    
    except: 
      print("Error with address: ", row['address_for_geocoding'])
    
    finally: 
      gdf_result.to_csv(PATH+"gdf_result_"+str(dist)+"m.csv")

  return gdf_result

In [ ]:
gdf_500m = add_osm_features(df_addr_rent, 500, tags, df_osm_obj)

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDepreca

In [ ]:
gdf_500m.shape

(105, 1048)

In [ ]:
gdf_1500m = add_osm_features(df_addr_rent, 1500, tags, df_osm_obj)

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDepreca

In [ ]:
gdf_1500m.shape

(105, 1048)

In [ ]:
# gdf_2000m = add_osm_features(df_addr_rent, 2000, tags, df_osm_obj)

In [ ]:
gdf_1000m = add_osm_features(df_addr_rent, 1000, tags, df_osm_obj)

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDepreca

In [ ]:
gdf_1000m.head()

0 highway_motorway_1000m highway_trunk_1000m  ...   latitude longtitude
1                    0.0                 0.0  ...  55.749452  37.537013
1                    0.0                 0.0  ...  55.748843  37.535369
1                    0.0                 0.0  ...  55.760470  37.519274
1                    0.0                 0.0  ...  55.782285  37.702644
1                    0.0                 0.0  ...  55.758778  37.612124

[5 rows x 1048 columns]

#### Load result for vacancies addresses


radius 500 m

In [ ]:
df_rent_500m = pd.read_csv(PATH+"gdf_result_"+str(500)+"m.csv")
df_rent_500m.head()

Unnamed: 0  highway_motorway_500m  ...   latitude  longtitude
0           1                    0.0  ...  55.749452   37.537013
1           1                    0.0  ...  55.748843   37.535369
2           1                    0.0  ...  55.760470   37.519274
3           1                    0.0  ...  55.782285   37.702644
4           1                    0.0  ...  55.758778   37.612124

[5 rows x 1049 columns]

In [ ]:
df_rent_500m.shape

(105, 1049)

radius 1000 m

In [ ]:
df_rent_1000m = pd.read_csv(PATH+"gdf_result_"+str(1000)+"m.csv")
df_rent_1000m.head()

Unnamed: 0  highway_motorway_1000m  ...   latitude  longtitude
0           1                     0.0  ...  55.749452   37.537013
1           1                     0.0  ...  55.748843   37.535369
2           1                     0.0  ...  55.760470   37.519274
3           1                     0.0  ...  55.782285   37.702644
4           1                     0.0  ...  55.758778   37.612124

[5 rows x 1049 columns]

In [ ]:
df_rent_1000m.shape

(105, 1049)

radius 1500 m

In [ ]:
df_rent_1500m = pd.read_csv(PATH+"gdf_result_"+str(1500)+"m.csv")
df_rent_1500m.head()

Unnamed: 0  highway_motorway_1500m  ...   latitude  longtitude
0           1                     0.0  ...  55.749452   37.537013
1           1                     0.0  ...  55.748843   37.535369
2           1                     0.0  ...  55.760470   37.519274
3           1                     0.0  ...  55.782285   37.702644
4           1                     0.0  ...  55.758778   37.612124

[5 rows x 1049 columns]

In [ ]:
df_rent_1500m.shape

(105, 1049)

#### Downloading OSM objects for offices

In [ ]:
offices_msc.head()

id    city  ...  building_residential_7lvlup  building_residential_7lvlup_500
3    3  Moscow  ...                          0.0                              1.0
6    6  Moscow  ...                          0.0                              0.0
7    7  Moscow  ...                          0.0                              2.0
13  13  Moscow  ...                          0.0                              0.0
16  16  Moscow  ...                          0.0                              0.0

[5 rows x 1273 columns]

In [ ]:
offices_msc.shape

(250, 1273)

In [ ]:
df_offices_msc = offices_msc[['id', 'ntb', 'lat', 'lon']].reset_index(drop=True)
df_offices_msc.columns = ['id', 'ntb', 'latitude', 'longtitude'] 
df_offices_msc.head()

id   ntb   latitude  longtitude
0   3  1308  55.685555   37.570230
1   6  2852  55.737389   37.617949
2   7  1888  55.723640   37.610586
3  13  1666  55.788474   37.537555
4  16  1735  55.893520   37.615400

In [ ]:
def add_osm_offices_features(df, dist, tags, df_dic_osm_obj): 

  gdf_result = gpd.GeoDataFrame()

  for idx, row in df.iterrows(): 

      print(idx, row['id']) # TEST 

      try: 
      
        gdf = ox.geometries.geometries_from_point((row['latitude'], row['longtitude']), tags, dist=dist).reset_index() 

        # Add center 
        gdf["centroid"] = gdf.geometry.centroid

        # coords of center
        gdf['lat_centre_of_object'] = gdf['centroid'].y
        gdf['lon_centre_of_object'] = gdf['centroid'].x
    
        # rent place address
        gdf['lat_chosen_address'] = row['latitude']
        gdf['lon_chosen_address'] = row['longtitude']

        # add dist column
        gdf['dist_to_chosen_address_km'] = gdf.apply(lambda row: calc_distance(row['lat_centre_of_object'], row['lon_centre_of_object'], row['lat_chosen_address'], row['lon_chosen_address']), axis=1)  

        # find osm object
        objs_around = agg_obj_around(gdf, dist, tags, df_dic_osm_obj)
      
        # transpose to row 
        objs_around = objs_around.T.reset_index(drop=True)
        new_header = objs_around.iloc[0] # grab the first row for the header
        objs_around = objs_around[1:]    # take the data less the header row
        objs_around.columns = new_header # set the header row as the df header

        # Add data 
        objs_around['id'] = row['id'] 
        objs_around['ntb'] = row['ntb']
        objs_around['latitude'] = row['latitude'] 
        objs_around['longtitude'] = row['longtitude']

        # add to result
        gdf_result = pd.concat([gdf_result, objs_around], axis=0)
      
      except: 
        print("Error with object - id: ", row['id'])
        break
        return gdf_result
      
      finally: 
        # Save result 
        gdf_result.to_csv(PATH+"gdf_offices_result_"+str(dist)+"m.csv")

  return gdf_result

In [ ]:
gdf_offices_msc_500m = add_osm_offices_features(df_offices_msc, 500, tags, df_osm_obj)

93 234.0


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:19: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



94 237.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:19: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



95 240.0


...

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:19: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



248 669.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:19: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



249 675.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:19: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [ ]:
gdf_offices_msc_500m.head()

0 highway_motorway_500m highway_trunk_500m  ...   latitude longtitude
1                   0.0                0.0  ...  55.728817  37.643483
1                   0.0                0.0  ...  55.669730  37.480478
1                   0.0                0.0  ...  55.773300  37.605771
1                   0.0                0.0  ...  55.890549  37.596599
1                   0.0                0.0  ...  55.662205  37.764431

[5 rows x 1048 columns]

In [ ]:
gdf_offices_msc_500m.shape

(157, 1048)

In [ ]:
gdf_offices_msc_1000m = add_osm_offices_features(df_offices_msc, 1000, tags, df_osm_obj)

0 3.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



1 6.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



2 7.0


...

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



22 59.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



23 60.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [ ]:
gdf_offices_msc_1000m.head()

0 highway_motorway_1000m highway_trunk_1000m  ...   latitude longtitude
1                    0.0                 0.0  ...  55.685555  37.570230
1                    0.0                 0.0  ...  55.737389  37.617949
1                    0.0                 0.0  ...  55.723640  37.610586
1                    0.0                 0.0  ...  55.788474  37.537555
1                    0.0                 4.0  ...  55.893520  37.615400

[5 rows x 1048 columns]

In [ ]:
gdf_offices_msc_1500m = add_osm_offices_features(df_offices_msc, 1500, tags, df_osm_obj)

0 3.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



1 6.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



2 7.0


...

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



248 669.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



249 675.0


/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [ ]:
gdf_offices_msc_1500m.shape

(250, 1048)

#### Load result for offices

radius 500 m

In [53]:
df_offices_msc_500m = pd.read_csv(PATH+"prepared_data/offices_features/gdf_offices_result_"+str(500)+"m.csv", index_col=[0])
df_offices_msc_500m.head()

id  ...  boundary_user_defined_500m
0   3.0  ...                         0.0
1   6.0  ...                         0.0
2   7.0  ...                         0.0
3  13.0  ...                         0.0
4  16.0  ...                         0.0

[5 rows x 1048 columns]

In [54]:
df_offices_msc_500m.tail()

id  ...  boundary_user_defined_500m
152  659.0  ...                         0.0
153  661.0  ...                         0.0
154  666.0  ...                         0.0
155  669.0  ...                         0.0
156  675.0  ...                         0.0

[5 rows x 1048 columns]

In [55]:
df_offices_msc_500m.shape

(250, 1048)

In [ ]:
df_offices_msc_500m.index.value_counts()

0      2
59     2
68     2
67     2
66     2
      ..
119    1
120    1
121    1
122    1
156    1
Length: 157, dtype: int64

radius 1000 m

In [47]:
df_offices_msc_1000m = pd.read_csv(PATH+"prepared_data/offices_features/gdf_offices_result_"+str(1000)+"m.csv", index_col=[0])
df_offices_msc_1000m.head()

id  ...  boundary_user_defined_1000m
0   3.0  ...                          0.0
1   6.0  ...                          0.0
2   7.0  ...                          0.0
3  13.0  ...                          0.0
4  16.0  ...                          0.0

[5 rows x 1048 columns]

In [48]:
df_offices_msc_1000m.shape

(250, 1048)

In [49]:
df_offices_msc_1000m.tail()

id  ...  boundary_user_defined_1000m
245  659.0  ...                          0.0
246  661.0  ...                          0.0
247  666.0  ...                          0.0
248  669.0  ...                          0.0
249  675.0  ...                          0.0

[5 rows x 1048 columns]

radius 1500 m

In [50]:
df_offices_msc_1500m = pd.read_csv(PATH+"prepared_data/offices_features/gdf_offices_result_"+str(1500)+"m.csv", index_col=[0])
df_offices_msc_1500m.head()

id  ...  boundary_user_defined_1500m
0   3.0  ...                          0.0
1   6.0  ...                          0.0
2   7.0  ...                          0.0
3  13.0  ...                          0.0
4  16.0  ...                          0.0

[5 rows x 1048 columns]

In [51]:
df_offices_msc_1500m.shape

(250, 1048)

In [52]:
df_offices_msc_1500m.tail()

id  ...  boundary_user_defined_1500m
245  659.0  ...                          0.0
246  661.0  ...                          0.0
247  666.0  ...                          0.0
248  669.0  ...                          0.0
249  675.0  ...                          0.0

[5 rows x 1048 columns]

#### id, target, lat, lon at the begining of dataframe

offices

In [ ]:
df_offices_msc_500m.head()

Unnamed: 0.1  highway_motorway_500m  ...   latitude  longtitude
0             1                    0.0  ...  55.685555   37.570230
1             1                    0.0  ...  55.737389   37.617949
2             1                    0.0  ...  55.723640   37.610586
3             1                    0.0  ...  55.788474   37.537555
4             1                    0.0  ...  55.893520   37.615400

[5 rows x 1049 columns]

In [ ]:
df_offices_msc_500m_ready = df_offices_msc_500m[['id', 'ntb', 'latitude', 'longtitude'] + [c for c in df_offices_msc_500m if c not in ['id', 'ntb', 'latitude', 'longtitude']]].drop(columns=['Unnamed: 0.1'])
df_offices_msc_500m_ready.head()

id  ...  boundary_user_defined_500m
0   3.0  ...                         0.0
1   6.0  ...                         0.0
2   7.0  ...                         0.0
3  13.0  ...                         0.0
4  16.0  ...                         0.0

[5 rows x 1048 columns]

In [ ]:
df_offices_msc_500m_ready.to_csv(PATH+"prepared_data/offices_features/gdf_offices_result_"+str(500)+"m.csv")

In [ ]:
df_offices_msc_1000m.head()

Unnamed: 0  highway_motorway_1000m  ...   latitude  longtitude
0           1                     0.0  ...  55.685555   37.570230
1           1                     0.0  ...  55.737389   37.617949
2           1                     0.0  ...  55.723640   37.610586
3           1                     0.0  ...  55.788474   37.537555
4           1                     0.0  ...  55.893520   37.615400

[5 rows x 1049 columns]

In [ ]:
df_offices_msc_1000m_ready = df_offices_msc_1000m[['id', 'ntb', 'latitude', 'longtitude'] + [c for c in df_offices_msc_1000m if c not in ['id', 'ntb', 'latitude', 'longtitude']]].drop(columns=['Unnamed: 0'])
df_offices_msc_1000m_ready.head()

id  ...  boundary_user_defined_1000m
0   3.0  ...                          0.0
1   6.0  ...                          0.0
2   7.0  ...                          0.0
3  13.0  ...                          0.0
4  16.0  ...                          0.0

[5 rows x 1048 columns]

In [ ]:
df_offices_msc_1000m_ready.to_csv(PATH+"prepared_data/offices_features/gdf_offices_result_"+str(1000)+"m.csv")

In [ ]:
df_offices_msc_1500m.head()

Unnamed: 0  highway_motorway_1500m  ...   latitude  longtitude
0           1                     0.0  ...  55.685555   37.570230
1           1                     0.0  ...  55.737389   37.617949
2           1                     0.0  ...  55.723640   37.610586
3           1                     0.0  ...  55.788474   37.537555
4           1                     0.0  ...  55.893520   37.615400

[5 rows x 1049 columns]

In [ ]:
df_offices_msc_1500m_ready = df_offices_msc_1500m[['id', 'ntb', 'latitude', 'longtitude'] + [c for c in df_offices_msc_1500m if c not in ['id', 'ntb', 'latitude', 'longtitude']]].drop(columns=['Unnamed: 0'])
df_offices_msc_1500m_ready.head()

id  ...  boundary_user_defined_1500m
0   3.0  ...                          0.0
1   6.0  ...                          0.0
2   7.0  ...                          0.0
3  13.0  ...                          0.0
4  16.0  ...                          0.0

[5 rows x 1048 columns]

In [ ]:
df_offices_msc_1500m_ready.to_csv(PATH+"prepared_data/offices_features/gdf_offices_result_"+str(1500)+"m.csv")

точки аренды

In [ ]:
# id_address_rent
df_addresses_prepared['id_address_rent'] = df_addresses_prepared.index
df_addresses_prepared.head()

address  ... id_address_rent
0  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...               0
1  Москва, ЦАО, р-н Пресненский, наб. Пресненская...  ...               1
2  Москва, СЗАО, р-н Хорошево-Мневники, Причальны...  ...               2
3  Москва, ВАО, р-н Соколиная гора, Большая Семен...  ...               3
4       Москва, ЦАО, р-н Тверской, Тверская ул., 8к1  ...               4

[5 rows x 11 columns]

In [ ]:
df_rent_500m.head()

Unnamed: 0  highway_motorway_500m  ...   latitude  longtitude
0           1                    0.0  ...  55.749452   37.537013
1           1                    0.0  ...  55.748843   37.535369
2           1                    0.0  ...  55.760470   37.519274
3           1                    0.0  ...  55.782285   37.702644
4           1                    0.0  ...  55.758778   37.612124

[5 rows x 1049 columns]

In [ ]:
df_rent_500m_ready = df_rent_500m[['id_address', 'address', 'latitude', 'longtitude'] + [c for c in df_rent_500m if c not in ['id_address', 'address', 'latitude', 'longtitude']]].drop(columns=['Unnamed: 0'])
df_rent_500m_ready.head()

id_address  ... boundary_user_defined_500m
0           0  ...                        0.0
1           1  ...                        0.0
2           2  ...                        0.0
3           3  ...                        0.0
4           4  ...                        0.0

[5 rows x 1048 columns]

In [ ]:
df_rent_500m_ready.to_csv(PATH+"prepared_data/rent_points_features/gdf_rent_result_"+str(500)+"m.csv")

In [ ]:
df_rent_1000m.head()

Unnamed: 0  highway_motorway_1000m  ...   latitude  longtitude
0           1                     0.0  ...  55.749452   37.537013
1           1                     0.0  ...  55.748843   37.535369
2           1                     0.0  ...  55.760470   37.519274
3           1                     0.0  ...  55.782285   37.702644
4           1                     0.0  ...  55.758778   37.612124

[5 rows x 1049 columns]

In [ ]:
df_rent_1000m_ready = df_rent_1000m[['id_address', 'address', 'latitude', 'longtitude'] + [c for c in df_rent_1000m if c not in ['id_address', 'address', 'latitude', 'longtitude']]].drop(columns=['Unnamed: 0'])
df_rent_1000m_ready.head()

id_address  ... boundary_user_defined_1000m
0           0  ...                         0.0
1           1  ...                         0.0
2           2  ...                         0.0
3           3  ...                         0.0
4           4  ...                         0.0

[5 rows x 1048 columns]

In [ ]:
df_rent_1000m_ready.to_csv(PATH+"prepared_data/rent_points_features/gdf_rent_result_"+str(1000)+"m.csv")

In [ ]:
df_rent_1500m.head()

Unnamed: 0  highway_motorway_1500m  ...   latitude  longtitude
0           1                     0.0  ...  55.749452   37.537013
1           1                     0.0  ...  55.748843   37.535369
2           1                     0.0  ...  55.760470   37.519274
3           1                     0.0  ...  55.782285   37.702644
4           1                     0.0  ...  55.758778   37.612124

[5 rows x 1049 columns]

In [ ]:
df_rent_1500m_ready = df_rent_1500m[['id_address', 'address', 'latitude', 'longtitude'] + [c for c in df_rent_1500m if c not in ['id_address', 'address', 'latitude', 'longtitude']]].drop(columns=['Unnamed: 0'])
df_rent_1500m_ready.head()

id_address  ... boundary_user_defined_1500m
0           0  ...                         0.0
1           1  ...                         0.0
2           2  ...                         0.0
3           3  ...                         0.0
4           4  ...                         0.0

[5 rows x 1048 columns]

In [ ]:
df_rent_1500m_ready.to_csv(PATH+"prepared_data/rent_points_features/gdf_rent_result_"+str(1500)+"m.csv")